<a href="https://colab.research.google.com/github/AgaZgo/peft_fine_tuning/blob/main/flan_t5_lora_ray_wandb.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# LoRA fine tuning of flan-T5 model for dialog summarization task

In [ ]:
!pip install \
    transformers==4.31.0 \
    datasets==2.14.4 \
    evaluate==0.4.0 \
    rouge_score==0.1.2 \
    peft==0.4.0 \
    loralib==0.1.1 \
    accelerate==0.21.0 \
    wandb==0.15.8 \
    ray[air]==2.6.1 \
    hyperopt==0.2.7 -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 19.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.3/519.3 kB 45.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 10.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.9/72.9 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.2/244.2 kB 26.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 82.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.9/56.9 MB 30.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 25.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 99.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 77.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 14.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 24.4 MB/s eta 0:00

In [2]:
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer, Seq2SeqTrainingArguments, Seq2SeqTrainer, EarlyStoppingCallback
from datasets import load_dataset
from peft import LoraConfig, get_peft_model

from ray import tune
from ray.tune.search.hyperopt import HyperOptSearch
from ray.air import RunConfig, session

from datetime import datetime

import numpy as np
import evaluate
import nltk
import torch
import wandb
import os

os.environ['WANDB_LOG_MODEL']='end' #save best model to W&B
os.environ['WANDB_PROJECT']='flan-t5-peft'
os.environ["WANDB_SILENT"] = "true"

nltk.download('punkt', quiet=True)

True

In [ ]:
wandb.login()

<IPython.core.display.Javascript object>

wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


<IPython.core.display.Javascript object>

wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


True

In [6]:
DATASET_NAME = 'knkarthick/dialogsum'
GPU = 'a100'
MODEL_SIZE = 'xl'

max_batchsize = {
    't4': {'base': 4,'large': 1},
    'a100': {'base': 8,'large': 4,'xl': 2} # to train 'xl' with batch_size==2 on a100(40GB), must use bfloat16
}  # values should be powers of 2

# arguments to be passed to train_model()
train_args = {
    'es_patience':3,  #early stopping patience
    'best_model_metric': 'eval_rougeLsum', #main model performance metric
    'per_device_train_batch_size': max_batchsize[GPU][MODEL_SIZE],
    'total_train_examples': 8192,
    'model_size': MODEL_SIZE
}

#arguments to be passed to tune.Tuner()
n_init_points = 10
time_budget_seconds = 60 * 60 * 15
num_trials = 25

In [7]:
def get_tokenized_dataset(dataset_name, model_size):
    dataset = load_dataset(dataset_name)
    model_name = f"google/flan-t5-{model_size}"
    tokenizer = AutoTokenizer.from_pretrained(model_name)

    def preprocess_data(examples):
        start_prompt = "Summarize the following dialogue:\n\n"
        end_prompt = "\n\nSummarize:"
        prompts = [start_prompt + dialogue + end_prompt for dialogue in examples['dialogue']]
        examples['input_ids'] = tokenizer(prompts, padding='max_length', truncation=True)['input_ids']
        examples['label'] = tokenizer(examples['summary'], padding='max_length', truncation=True)['input_ids']
        examples['label'] = [
            [-100 if token==tokenizer.pad_token_id else token for token in label] for label in examples['label']
        ]
        return examples

    dataset_tokenized = dataset.map(preprocess_data, batched=True)
    dataset_tokenized.set_format('torch')

    return dataset_tokenized

train_args['dataset'] = get_tokenized_dataset(DATASET_NAME, MODEL_SIZE)

In [8]:
def train_model(config, params):

    run_name = session.get_trial_name()  #we want to have the same name for ray trial and wandb run
    wandb.init(name=run_name, config=config)

    model_name = f"google/flan-t5-{params['model_size']}"
    base_model = AutoModelForSeq2SeqLM.from_pretrained(model_name, device_map='auto', torch_dtype=torch.bfloat16)  # bf16 only for Ampere GPU
    tokenizer = AutoTokenizer.from_pretrained(model_name)

    rouge = evaluate.load('rouge')

    def compute_metrics(eval_preds):
        preds, labels = eval_preds

        labels = np.where(labels!=-100, labels, tokenizer.pad_token_id)
        decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)
        decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)

        # sentences seperated with '\n' as required by rougeLsum
        decoded_preds = ["\n".join(nltk.sent_tokenize(preds.strip())) for preds in decoded_preds]
        decoded_labels = ["\n".join(nltk.sent_tokenize(labels.strip())) for labels in decoded_labels]

        results =  rouge.compute(predictions=decoded_preds, references=decoded_labels, use_stemmer=True)

        return results

    early_stopping = EarlyStoppingCallback(early_stopping_patience=params['es_patience'])

    output_dir = f"./lora_training/{run_name}"

    lora_params = {
        'r': config['lora_r'],
        'lora_alpha': config['lora_alpha'],
        'target_modules': ['q', 'v'],
        'lora_dropout': 0.05,
        'bias': 'none',
        'task_type': "SEQ_2_SEQ_LM"
    }

    lora_config = LoraConfig(**lora_params)

    lora_model = get_peft_model(
        base_model,
        lora_config
    )

    lora_training_args = Seq2SeqTrainingArguments(
        output_dir=output_dir,
        learning_rate=config['learning_rate'],
        per_device_train_batch_size=min(params['per_device_train_batch_size'], config['effective_batch_size']),
        gradient_accumulation_steps=max(1, config['effective_batch_size']//params['per_device_train_batch_size']),
        max_steps=params['total_train_examples']//config['effective_batch_size'],
        logging_steps=1024/config['effective_batch_size'],
        evaluation_strategy='steps',
        save_steps=1024/config['effective_batch_size'],
        logging_dir=output_dir+"/logs",
        predict_with_generate=True,
        load_best_model_at_end=True,
        metric_for_best_model=params['best_model_metric'],
        disable_tqdm=True,
        bf16=True,
        report_to='wandb',
        run_name=run_name
    )

    lora_trainer = Seq2SeqTrainer(
        model=lora_model,
        args=lora_training_args,
        train_dataset=params['dataset']['train'],
        eval_dataset=params['dataset']['validation'],
        tokenizer=tokenizer,
        compute_metrics=compute_metrics,
        callbacks=[early_stopping]
    )

    lora_trainer.train()
    result = {params['best_model_metric']: lora_trainer.state.best_metric}
    wandb.finish()
    return result

In [9]:
train_model = tune.with_resources(
    tune.with_parameters(
        train_model,
        params = train_args
    ),
    {"gpu": 1, 'cpu':12}
)

In [10]:
search_space = {
    'lora_r': tune.randint(8,25),
    'lora_alpha': tune.quniform(1,25,0.5),
    'effective_batch_size': tune.choice([8,16,32]),  # powers of 2 recommended
    'learning_rate': tune.qloguniform(1e-4,1e-2,5e-5)
}

tune_config = tune.TuneConfig(
    num_samples=num_trials,
    search_alg=HyperOptSearch(metric='eval_rougeLsum', mode='max', n_initial_points=n_init_points),
    time_budget_s=time_budget_seconds,
    trial_name_creator = lambda trial: f"lora_{trial.trial_id}_{datetime.now().strftime('%m%d%H%M')}"
)

run_config = RunConfig(
    storage_path="./ray"
)

tuner = tune.Tuner(
    train_model,
    param_space=search_space,
    tune_config=tune_config,
    run_config=run_config
)

In [11]:
tuner.fit()

2023-09-03 18:58:43,382	INFO worker.py:1612 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 
2023-09-03 18:58:44,756	INFO tune.py:226 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `Tuner(...)`.
2023-09-03 18:58:44,758	INFO tune.py:666 -- [output] This will use the new output engine with verbosity 1. To disable the new output and use the legacy output engine, set the environment variable RAY_AIR_NEW_OUTPUT=0. For more information, please see https://github.com/ray-project/ray/issues/36949


+--------------------------------------------------------------------+
| Configuration for experiment     train_model_2023-09-03_18-58-23   |
+--------------------------------------------------------------------+
| Search algorithm                 SearchGenerator                   |
| Scheduler                        FIFOScheduler                     |
| Number of trials                 25                                |
+--------------------------------------------------------------------+

View detailed results here: /content/ray/train_model_2023-09-03_18-58-23
To visualize your results with TensorBoard, run: `tensorboard --logdir /content/ray/train_model_2023-09-03_18-58-23`

Trial status: 1 PENDING
Current time: 2023-09-03 18:58:44. Total running time: 0s
Logical resource usage: 0/12 CPUs, 0/1 GPUs (0.0/1.0 accelerator_type:A100)
+--------------------------------------------------------------------------------------------------------+
| Trial name               status       lora_r

(pid=86394) 2023-09-03 18:58:50.677048: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


Trial lora_ae121055_09031858 started with configuration:
+------------------------------------------------+
| Trial lora_ae121055_09031858 config            |
+------------------------------------------------+
| effective_batch_size                         8 |
| learning_rate                           0.0001 |
| lora_alpha                                 3.5 |
| lora_r                                      21 |
+------------------------------------------------+



Loading checkpoint shards: 100%|██████████| 2/2 [00:10<00:00,  5.19s/it]


...

Loading checkpoint shards: 100%|██████████| 2/2 [00:06<00:00,  3.40s/it]
(train_model pid=86394) /usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
(train_model pid=86394)   warnings.warn(
(train_model pid=86394) You're using a T5TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


Trial status: 23 TERMINATED | 1 RUNNING | 1 PENDING
Current time: 2023-09-04 07:38:08. Total running time: 12hr 39min 23s
Logical resource usage: 12.0/12 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:A100)
+---------------------------------------------------------------------------------------------------------------------------------------------------------+
| Trial name               status         lora_r     lora_alpha     effective_batch_size     learning_rate     iter     total time (s)     eval_rougeLsum |
+---------------------------------------------------------------------------------------------------------------------------------------------------------+
| lora_be5a3075_09040702   RUNNING            16           16.5                       32           0.00155                                                |
| lora_ae121055_09031858   TERMINATED         21            3.5                        8           0.0001         1            2108.43           0.373378 |
| lora_f688747c_0

Loading checkpoint shards: 100%|██████████| 2/2 [00:06<00:00,  3.46s/it]
(train_model pid=86394) /usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
(train_model pid=86394)   warnings.warn(
(train_model pid=86394) You're using a T5TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


Trial status: 24 TERMINATED | 1 RUNNING
Current time: 2023-09-04 08:13:13. Total running time: 13hr 14min 28s
Logical resource usage: 12.0/12 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:A100)
+---------------------------------------------------------------------------------------------------------------------------------------------------------+
| Trial name               status         lora_r     lora_alpha     effective_batch_size     learning_rate     iter     total time (s)     eval_rougeLsum |
+---------------------------------------------------------------------------------------------------------------------------------------------------------+
| lora_652d4a68_09040737   RUNNING            18           20                         32           0.00075                                                |
| lora_ae121055_09031858   TERMINATED         21            3.5                        8           0.0001         1            2108.43           0.373378 |
| lora_f688747c_09031858   TE

ResultGrid<[
  Result(
    metrics={'eval_rougeLsum': 0.3733780542041913, 'done': True, 'trial_id': 'ae121055', 'experiment_tag': '1_effective_batch_size=8,learning_rate=0.0001,lora_alpha=3.5000,lora_r=21'},
    path='/content/ray/train_model_2023-09-03_18-58-23/lora_ae121055_09031858_1_effective_batch_size=8,learning_rate=0.0001,lora_alpha=3.5000,lora_r=21_2023-09-03_18-58-44',
    checkpoint=None
  ),
  Result(
    metrics={'eval_rougeLsum': 0.3836071390788707, 'done': True, 'trial_id': 'f688747c', 'experiment_tag': '2_effective_batch_size=8,learning_rate=0.0003,lora_alpha=2.5000,lora_r=11'},
    path='/content/ray/train_model_2023-09-03_18-58-23/lora_f688747c_09031858_2_effective_batch_size=8,learning_rate=0.0003,lora_alpha=2.5000,lora_r=11_2023-09-03_18-58-52',
    checkpoint=None
  ),
  Result(
    metrics={'eval_rougeLsum': 0.3963346684602575, 'done': True, 'trial_id': 'c0fd03d1', 'experiment_tag': '3_effective_batch_size=32,learning_rate=0.0036,lora_alpha=13.0000,lora_r=21'},
  